In [ ]:
import awswrangler as wr
import pandas as pd
import numpy as np
import boto3
# from sagemaker import get_execution_role
import datetime
import string
import random

# role = get_execution_role()

# 측정치
1. 총 5가지 측정치가 있음 (Temperature, Humidity, illumination, motiondetect, dooropen)
2. 연구소 회의실의 측정치는 5가지 측정치가 동시에 기록되어 있는 경우가 없으므로 제외
3. 2-3 회의실의 측정치에서 약 20일간 동시에 측정되어 있음 (9월초, 10월말, 11월 초)
4. 2-3 회의의 측정치를 기준으로 훈련데이터 생성 진행

# Temperature, Humidity, illumination preprocessing
1. 기존 초 단위의 측정 시간을 1분 단위로 변경
2. 동일 시간 인덱스에 여러 값이 있을 경우 Median 값을 취함
3. 결측치가 있을 경우 이전 측정치중 마지막 값으로 채움 (ffill)
4. 이전 측정치가 없을 경우 자신의 값으로 이전 값들을 채움 (bfill)

In [ ]:
# Temperature, Humidity preprocessing
temphum_df = pd.read_csv('temperature_humidity.csv')
temphum_df['timestamp'] = pd.to_datetime(temphum_df.timestamp)
df_temp_hum = temphum_df[   temphum_df['device_id'].isin(['00158d00028d93d8'])  ]
df_temp_hum.set_index('timestamp', inplace=True)
df_temp_hum = df_temp_hum.resample(rule='T').median().fillna(method='ffill').fillna(method='bfill')
df_temp_hum = df_temp_hum[['hum', 'temp']].fillna(method='ffill').fillna(method='bfill')
df_temp_hum


In [ ]:
# illumination preprocessing
tmp = pd.read_csv('illumination.csv')
tmp['timestamp'] = pd.to_datetime(tmp.timestamp)
tmp.rename(columns={'evt':'illum'}, inplace=True)
df_illumination = tmp[   tmp['device_id'].isin(['00158d0006c9d5ed'])  ]
df_illumination.set_index('timestamp', inplace=True)
df_illumination = df_illumination.resample(rule='T').median()#[['device_id', 'hum', 'temp']]
df_illumination = df_illumination[['illum']].fillna(method='ffill').fillna(method='bfill')
df_illumination = df_illumination.join(df_temp_hum)
df_illumination

# motion, door preprocessing
1. 기존 초 단위의 측정 시간을 1분 단위로 변경
2. 동일 시간 인덱스에 여러 값이 있을 경우 count 값을 취함
3. 결측치가 있을 경우 0 (zero) 값으로 채움

# data merge
1. 5가지 측정치를 1개의 테이블로 합침
2. 한번에 5개 측정치를 concat() 할경우 time index 가 중복되기 때문에 순차적으로 1:1 concat 을 실행

# data label
1. 측정치와 마챦가지로 1개의 컬럼에 기록하여 측정치 테이블과 merge 함
2. ~~결측치의 경우 linear interpolation 으로 복구~~
3. 결측치 처리
   1. 라벨의 not detected(날짜/시간 인식못함) 값은 임의로 날짜를 2000년으로 수정해 놓았음 -> 날짜 필터를 이용하여 제거
   2. 제거된 부분의 값은 0 값으로 채워넣음

In [ ]:
# motion, door preprocessing
tmp = pd.read_csv('motion_door.csv')
tmp['timestamp'] = pd.to_datetime(tmp.timestamp)
tmp.set_index('timestamp', inplace=True)

df_motion = tmp[tmp.device_id == '00158d0002d545b4'].copy()
df_motion.rename(columns={'evt':'motion'}, inplace=True)
df_motion = df_motion.resample(rule='T').count()

df_door = tmp[tmp.device_id == '00158d0005bb96f3'].copy()
df_door.rename(columns={'evt':'door'}, inplace=True)
df_door = df_door.resample(rule='T').count()

df_motion_door = pd.concat([df_motion, df_door])[['motion', 'door']].fillna(value=0)
df_merge = df_motion_door.join(df_illumination)
df_merge.to_csv('df_merge.csv')
df_merge

In [ ]:
# read and merge label
df_l1 = pd.read_csv('20210830_080618A.csv')
df_l2 = pd.read_csv('20211025_080015A.csv')
df_label = pd.concat([df_l1, df_l2], ignore_index=True)
df_label.rename(columns={df_label.columns[1]:'timestamp', df_label.columns[2]:'label'}, inplace=True)
df_label['timestamp'] = pd.to_datetime(df_label.timestamp)
# filtering
df_label = df_label.loc[ (df_label['timestamp'] > '2021-01-01') ]
df_label.set_index('timestamp', inplace=True)
# resampling
df_label = df_label.resample(rule='T').max()
df_label = df_label[['label']]

df_label = df_merge.join(df_label).resample(rule='T').max()
df_label_8030_0916 = df_label.loc[ '2021-08-30 08:00': '2021-09-16 18:00'].fillna(value=0)
df_label_1025_1103 = df_label.loc[ '2021-10-25 08:00': '2021-11-03 18:00'].fillna(value=0)
df_label.to_csv('df_labeled.csv')
df_label_1025_1103.to_csv('df_label_1025_1103.csv')
df_label_8030_0916.to_csv('df_label_8030_0916.csv')
